In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load in 

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import matplotlib.pyplot as plt
import xgboost as xgb
from xgboost import XGBClassifier, XGBRegressor
from xgboost import plot_importance
from matplotlib import pyplot
# import shap

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# Any results you write to the current directory are saved as output.
from time import time
from tqdm import tqdm_notebook as tqdm
from collections import Counter
from scipy import stats
import lightgbm as lgb
from sklearn.metrics import cohen_kappa_score
from sklearn.model_selection import KFold, StratifiedKFold,GroupKFold
import gc
import json
pd.set_option('display.max_columns', 1000)
pd.options.display.max_rows=1000
pd.options.display.max_colwidth=200
import warnings
warnings.filterwarnings(action='ignore')
from sklearn.metrics import mean_squared_error
from sklearn  import metrics
from functools import partial
import scipy as sp

import csv
import gc
gc.enable()
from collections import OrderedDict
import subprocess


/kaggle/input/dsb-datasets/test_extras.pkl
/kaggle/input/dsb-datasets/train_extras.pkl
/kaggle/input/data-science-bowl-2019/sample_submission.csv
/kaggle/input/data-science-bowl-2019/test.csv
/kaggle/input/data-science-bowl-2019/train.csv
/kaggle/input/data-science-bowl-2019/train_labels.csv
/kaggle/input/data-science-bowl-2019/specs.csv


In [2]:
DTYPES_RAW = {
    'event_id': 'object',
    'game_session': 'object',
    'installation_id': 'object',
    'event_count': np.uint16,
    'event_code': np.uint16,
    'game_time': np.uint32,
    'type': 'category',
    'world': 'category',
    'title': 'category',  
}

FIELDS = {
    # Extras from JSON
    # If you add more data, do not forget
    # to add default values below.
    'level': np.uint8,
    'round': np.uint8,
    'correct': np.int8,
    'misses': np.int8,
    'exit_type':'object',
    'time_duration':np.int64,
    'time_played':np.int64
    
    # Nested object separated by '_'
    # for example: {'coordinates': {'x': 12, 'y': 12}}
    # 'coordinates_x': np.uint16
    # 'coordinates_y': np.uint16
}

DTYPES = OrderedDict( (dt[0], (dt[1], i)) for i, dt in enumerate(FIELDS.items()))

import subprocess

def file_len(fname):
    """Returns the number of lines in a file.
       @see: https://www.kaggle.com/szelee/how-to-import-a-csv-file-of-55-million-rows
    """
    p = subprocess.Popen(['wc', '-l', fname], stdout=subprocess.PIPE, 
                                              stderr=subprocess.PIPE)
    result, err = p.communicate()
    if p.returncode != 0:
        raise IOError(err)
    return int(result.strip().split()[0])+1


def flatten(dct, res, separator='_'):
    """Flatten a dictionary.
       @see: https://stackoverflow.com/a/34094630/4158850
    """
    queue = [('', dct)]

    while queue:
        prefix, d = queue.pop()
        for k, v in d.items():
            key = prefix + k
            if not isinstance(v, dict):
                if key in FIELDS.keys():
                    res[0][DTYPES[key][1]] = v
            else:
                queue.append((key + separator, v))

    return res

def records_from_json(fh, n_rows, event_ids_to_drop):
    """Yields the records from a file object."""
    rows = csv.reader(fh, delimiter=',')
    skip_header = next(rows)
    
    # define dtype for more memory-efficiency.
    dtype = dict(names=list(FIELDS.keys()), formats=list(FIELDS.values()))
    defrow = np.zeros((1,), dtype=dtype)

    for event_id, game_session, timestamp, event_data, installation_id, event_count, event_code, game_time, title, typ, world in tqdm(rows, total=n_rows):
        
        # It is more memory-efficient if we don't use the the train df's columns yet.
        row = defrow.copy()

        # Default (required because of the copy above) values for the extracted data
        # you can use np.nan too (in this case the dtype should be np.float64)
        row[0][DTYPES['level'][1]] = 0
        row[0][DTYPES['round'][1]] = 0
        row[0][DTYPES['correct'][1]] = -1
        row[0][DTYPES['misses'][1]] = -1

        if event_id not in event_ids_to_drop:
            row = flatten(json.loads(event_data), row)

        yield row[0]

def from_records(path, event_ids_to_drop):
    n_rows = file_len(path)
    with open(path) as fh:
        return pd.DataFrame.from_records(records_from_json(fh, n_rows, event_ids_to_drop))

specs = pd.read_csv('/kaggle/input/data-science-bowl-2019/specs.csv')
specs.args = specs.args.apply(lambda x: json.loads(str(x)))
eventIdsToDrop = []

for _, spec in specs.iterrows():
    j = pd.io.json.json_normalize(spec.args)
    vals = j.loc[(j.name.isin(FIELDS.keys()))].name.values

    if len(vals) == 0:
        eventIdsToDrop += [spec.event_id]

set(eventIdsToDrop)
print(len(eventIdsToDrop))

for _, spec in specs.iterrows():
    j = pd.io.json.json_normalize(spec.args)
    vals = j.loc[(j.name.isin(FIELDS.keys()))].name.values

    if len(vals) == 0:
        eventIdsToDrop += [spec.event_id]



extras_df = from_records('/kaggle/input/data-science-bowl-2019/train.csv', eventIdsToDrop)

train_df = pd.read_csv('/kaggle/input/data-science-bowl-2019/train.csv', parse_dates=['timestamp'], dtype=DTYPES_RAW, usecols=['timestamp'] + list(DTYPES_RAW.keys()))
train_df = train_df.merge(extras_df, left_index=True, right_index=True)
train_df.info()

train_df.to_pickle('train_extras.pkl')


del extras_df
del train_df
gc.collect()

%reset -f Out


extras_df = from_records('/kaggle/input/data-science-bowl-2019/test.csv', eventIdsToDrop)
test_df = pd.read_csv('/kaggle/input/data-science-bowl-2019/test.csv', parse_dates=['timestamp'], dtype=DTYPES_RAW, usecols=['timestamp'] + list(DTYPES_RAW.keys()))
test_df = test_df.merge(extras_df, left_index=True, right_index=True)

test_df.to_pickle('test_extras.pkl')

del extras_df
del test_df
gc.collect()

%reset -f Out

146



<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11341042 entries, 0 to 11341041
Data columns (total 17 columns):
event_id           object
game_session       object
timestamp          datetime64[ns, UTC]
installation_id    object
event_count        uint16
event_code         uint16
game_time          uint32
title              category
type               category
world              category
level              uint8
round              uint8
correct            int8
misses             int8
exit_type          object
time_duration      int64
time_played        int64
dtypes: category(3), datetime64[ns, UTC](1), int64(2), int8(2), object(4), uint16(2), uint32(1), uint8(2)
memory usage: 767.9+ MB
Flushing output cache (0 entries)



Flushing output cache (0 entries)


In [3]:
clip_time = {'Welcome to Lost Lagoon!':19,'Tree Top City - Level 1':17,'Ordering Spheres':61, 'Costume Box':61,
        '12 Monkeys':109,'Tree Top City - Level 2':25, 'Pirate\'s Tale':80, 'Treasure Map':156,'Tree Top City - Level 3':26,
        'Rulers':126, 'Magma Peak - Level 1':20, 'Slop Problem':60, 'Magma Peak - Level 2':22, 'Crystal Caves - Level 1':18,
        'Balancing Act':72, 'Lifting Heavy Things':118,'Crystal Caves - Level 2':24, 'Honey Cake':142, 'Crystal Caves - Level 3':19,
        'Heavy, Heavier, Heaviest':61}

# Objective

* In the last notebook we create our baseline model including a feature selection part. 
* Cohen cappa score of 0.456 (lb) with a local cv score of 0.529
* In this notebook we are going to add more features and remove others that i think they overfitt the train set and then check if our local cv score improve.
* Next, we will check if this improvement aligns with the lb.

# Notes
* Check the distribution of the target variable of the out of folds score and the prediction distribution. A good model should more or less have the same distribution.

In [4]:
Id = "installation_id"
target = "accuracy_group"

In [5]:
def eval_qwk_lgb_regr(y_true, y_pred):
    """
    Fast cappa eval function for lgb.
    """
    dist = Counter(reduce_train['accuracy_group'])
    for k in dist:
        dist[k] /= len(reduce_train)
#     reduce_train['accuracy_group'].hist()
    
    acum = 0
    bound = {}
    for i in range(3):
        acum += dist[i]
        bound[i] = np.percentile(y_pred, acum * 100)

    def classify(x):
        if x <= bound[0]:
            return 0
        elif x <= bound[1]:
            return 1
        elif x <= bound[2]:
            return 2
        else:
            return 3

    y_pred = np.array(list(map(classify, y_pred))).reshape(y_true.shape)

    return 'cappa', cohen_kappa_score(y_true, y_pred, weights='quadratic'), True

In [6]:
def cohenkappa(ypred, y):
    y = y.get_label().astype("int")
    ypred = ypred.reshape((4, -1)).argmax(axis = 0)
    loss = cohenkappascore(y, y_pred, weights = 'quadratic')
    return "cappa", loss, True

In [7]:
train_labels = pd.read_csv('/kaggle/input/data-science-bowl-2019/train_labels.csv')
specs = pd.read_csv('/kaggle/input/data-science-bowl-2019/specs.csv')
train = pd.read_pickle('train_extras.pkl')
test = pd.read_pickle('test_extras.pkl')
sample_submission = pd.read_csv('/kaggle/input/data-science-bowl-2019/sample_submission.csv')

In [8]:

def encode_title(train, test, train_labels):
    # encode title
    train['title_event_code'] = list(map(lambda x, y: str(x) + '_' + str(y), train['title'], train['event_code']))
    test['title_event_code'] = list(map(lambda x, y: str(x) + '_' + str(y), test['title'], test['event_code']))
    all_title_event_code = sorted(list(set(train["title_event_code"].unique()).union(test["title_event_code"].unique())))
    # make a list with all the unique 'titles' from the train and test set
    list_of_user_activities = sorted(list(set(train['title'].unique()).union(set(test['title'].unique()))))
    # make a list with all the unique 'event_code' from the train and test set
    list_of_event_code = sorted(list(set(train['event_code'].unique()).union(set(test['event_code'].unique()))))
    list_of_event_id = sorted(list(set(train['event_id'].unique()).union(set(test['event_id'].unique()))))
    # make a list with all the unique worlds from the train and test set
    list_of_worlds = sorted(list(set(train['world'].unique()).union(set(test['world'].unique()))))
    # create a dictionary numerating the titles
    activities_map = dict(zip(list_of_user_activities, np.arange(len(list_of_user_activities))))
    activities_labels = dict(zip(np.arange(len(list_of_user_activities)), list_of_user_activities))
    activities_world = dict(zip(list_of_worlds, np.arange(len(list_of_worlds))))
    assess_titles = sorted(list(set(train[train['type'] == 'Assessment']['title'].value_counts().index).union(set(test[test['type'] == 'Assessment']['title'].value_counts().index))))
    # replace the text titles with the number titles from the dict
    train['title'] = train['title'].map(activities_map)
    test['title'] = test['title'].map(activities_map)
    train['world'] = train['world'].map(activities_world)
    test['world'] = test['world'].map(activities_world)
    train_labels['title'] = train_labels['title'].map(activities_map)
    win_code = dict(zip(activities_map.values(), (4100*np.ones(len(activities_map))).astype('int')))
    # then, it set one element, the 'Bird Measurer (Assessment)' as 4110, 10 more than the rest
    win_code[activities_map['Bird Measurer (Assessment)']] = 4110
    # convert text into datetime
    train['timestamp'] = pd.to_datetime(train['timestamp'])
    test['timestamp'] = pd.to_datetime(test['timestamp'])
    train['hour'] = train['timestamp'].dt.hour
    test['hour'] = test['timestamp'].dt.hour
    train['weekday'] = train['timestamp'].dt.weekday
    test['weekday'] = test['timestamp'].dt.weekday
    return train, test, train_labels, win_code, list_of_user_activities, list_of_event_code, activities_labels, assess_titles, list_of_event_id, all_title_event_code

In [9]:
# get usefull dict with maping encode
train, test, train_labels, win_code, list_of_user_activities, list_of_event_code, activities_labels, assess_titles, list_of_event_id, all_title_event_code = encode_title(train, test, train_labels)


#### save to pickle and reload

In [10]:
# tag = "encode_title"

# # train
# result_path = "../temp/train_" + tag + ".pkl"
# train.to_pickle(result_path)

# # test
# result_path = "../temp/test_" + tag + ".pkl"
# test.to_pickle(result_path)

In [11]:
# tag = "encode_title"
# train = pd.read_pickle("../temp/train_" + tag + ".pkl")
# test = pd.read_pickle("../temp/test_" + tag + ".pkl")

# print('Reading sample_submission.csv file....')
# sample_submission = pd.read_csv(input_path + 'sample_submission.csv')
# print('Sample_submission.csv file have {} rows and {} columns'.format(sample_submission.shape[0], sample_submission.shape[1]))


In [12]:
"Cauldron Filler (Assessment)","Chest Sorter (Assessment)','Bird Measurer (Assessment)","Cart Balancer (Assessment)","Mushroom Sorter (Assessment)"

('Cauldron Filler (Assessment)',
 "Chest Sorter (Assessment)','Bird Measurer (Assessment)",
 'Cart Balancer (Assessment)',
 'Mushroom Sorter (Assessment)')

In [13]:
train.head()

event_id      game_session                        timestamp  \
0  27253bdc  45bb1e1b6b50c07b 2019-09-06 17:53:46.937000+00:00   
1  27253bdc  17eeb7f223665f53 2019-09-06 17:54:17.519000+00:00   
2  77261ab5  0848ef14a8dc6892 2019-09-06 17:54:56.302000+00:00   
3  b2dba42b  0848ef14a8dc6892 2019-09-06 17:54:56.387000+00:00   
4  1bb5fbdb  0848ef14a8dc6892 2019-09-06 17:55:03.253000+00:00   

  installation_id  event_count  event_code  game_time title      type world  \
0        0001e90f            1        2000          0    43      Clip     2   
1        0001e90f            1        2000          0    28      Clip     1   
2        0001e90f            1        2000          0    35  Activity     1   
3        0001e90f            2        3010         53    35  Activity     1   
4        0001e90f            3        3110       6972    35  Activity     1   

   level  round  correct  misses exit_type  time_duration  time_played  \
0      0      0       -1      -1         0              0            0   
1      0      0       -1      -1         0              0            0   
2      0      0       -1      -1         0              0            0   
3      0      0       -1      -1         0              0            0   
4      0      0       -1      -1         0              0            0   

                     title_event_code  hour  weekday  
0        Welcome to Lost Lagoon!_2000    17        4  
1           Magma Peak - Level 1_2000    17        4  
2  Sandcastle Builder (Activity)_2000    17        4  
3  Sandcastle Builder (Activity)_3010    17        4  
4  Sandcastle Builder (Activity)_3110    17        4

In [14]:
# this is the function that convert the raw data into processed features
def get_data(user_sample, test_set=False):
    '''
    The user_sample is a DataFrame from train or test where the only one 
    installation_id is filtered
    And the test_set parameter is related with the labels processing, that is only requered
    if test_set=False
    '''
    # Constants and parameters declaration
    last_activity = 0
    clip_duration = 0
    game_duration = 0
    activity_duration = 0
    user_activities_count = {'Clip':0, 'Activity': 0, 'Assessment': 0, 'Game':0}
    Activity_sum_event_count = 0
    game_sum_event_count = 0
    # new features: time spent in each activity
    last_session_time_sec = 0
    accuracy_groups = {0:0, 1:0, 2:0, 3:0}
    all_assessments = []
    accumulated_accuracy_group = 0
    accumulated_accuracy = 0
    accumulated_correct_attempts = 0 
    accumulated_uncorrect_attempts = 0
    accumulated_actions = 0
    counter = 0
    time_first_activity = float(user_sample['timestamp'].values[0])
    durations = []
    last_accuracy_title = {'acc_' + title: -1 for title in assess_titles}
    event_code_count: Dict[str, int] = {ev: 0 for ev in list_of_event_code}
    event_id_count: Dict[str, int] = {eve: 0 for eve in list_of_event_id}
    title_count: Dict[str, int] = {eve: 0 for eve in activities_labels.values()} 
    title_event_code_count: Dict[str, int] = {t_eve: 0 for t_eve in all_title_event_code}
    game_event_code_count: Dict[str, int] = { str(ev) + '_g': 0 for ev in list_of_event_code}
    Activity_event_code_count: Dict[str, int] = {str(ev) + '_A': 0 for ev in list_of_event_code}
    assessment_completed = 0
    CumCount_assessment_completed = 0 
    # last features
    sessions_count = 0
    cauldron_Filler_assesment = '' 
    chest_sorter =''
    bird_measurer =''
    cart_balancer =''
    mushroom_sorter = ''
    prev_accuracy =''
    
    clip_counter = 0
    game_counter =0
    activity_counter = 0
    CumCount_game_completed =0 
    
   
    
    
    clip_durations_list = []
    clip_durations = []
    cumsum_clip_duration=0
    activity_durations_list = []
    activity_durations =[]
    cumsum_activity_duration=0
    game_durations_list = []
    game_durations= []
    cumsum_game_duration=0
    
    misses_true = 0
    misses_false = 0
    correct_true = 0
    correct_false = 0 
    game_correct_list = [-1]
    game_round_list = [-1]
    game_level_list = [-1]
    game_misses_list = [-1]
    
    
    
    
    
    # itarates through each session of one instalation_id
    for i, session in user_sample.groupby('game_session', sort=False):
        # i = game_session_id
        # session is a DataFrame that contain only one game_session
        
        # get some sessions information
        session_type = session['type'].iloc[0]
        session_title = session['title'].iloc[0]
        session_title_text = activities_labels[session_title]
                    
        # for each assessment, and only this kind off session, the features below are processed
        # and a register are generated
        if (session_type == 'Assessment') & (test_set or len(session)>1):
            # search for event_code 4100, that represents the assessments trial
            all_attempts = session.query(f'event_code == {win_code[session_title]}')
            # then, check the numbers of wins and the number of losses
            true_attempts = all_attempts[all_attempts['correct']==1].shape[0]
            false_attempts = all_attempts[all_attempts['correct']==0].shape[0]
            # copy a dict to use as feature template, it's initialized with some itens: 
            # {'Clip':0, 'Activity': 0, 'Assessment': 0, 'Game':0}
            features = user_activities_count.copy()
            features.update(last_accuracy_title.copy())
            features.update(event_code_count.copy())
            features.update(event_id_count.copy())
            features.update(title_count.copy())
            features.update(title_event_code_count.copy())
            features.update(last_accuracy_title.copy())
            features['installation_session_count'] = sessions_count
            #features["4070"] = event_code_count[4070]
            #features['hour'] = session['hour'].iloc[-1]
            #features['weekday'] = session['weekday'].iloc[-1]
            variety_features = [('var_event_code', event_code_count),
                              ('var_event_id', event_id_count),
                               ('var_title', title_count),
                               ('var_title_event_code', title_event_code_count)]
            
            for name, dict_counts in variety_features:
                arr = np.array(list(dict_counts.values()))
                features[name] = np.count_nonzero(arr)
            # get installation_id for aggregated features
            features['installation_id'] = session['installation_id'].iloc[-1]
            # add title as feature, remembering that title represents the name of the game
            features['session_title'] = session['title'].iloc[0]
            # the 4 lines below add the feature of the history of the trials of this player
            # this is based on the all time attempts so far, at the moment of this assessment
            features['accumulated_correct_attempts'] = accumulated_correct_attempts
            features['accumulated_uncorrect_attempts'] = accumulated_uncorrect_attempts
            features['assessment_type'] = session_title_text
            accumulated_correct_attempts += true_attempts 
            accumulated_uncorrect_attempts += false_attempts
            features.update(game_event_code_count.copy())
            features.update(Activity_event_code_count.copy())
            features['game_sum_event_count'] = game_sum_event_count
            features['Activity_sum_event_count'] = Activity_sum_event_count
            # the time spent in the app so far
            if durations == []:
                features['duration_mean'] = 0
                features['duration_std'] = 0
            else:
                features['duration_mean'] = np.mean(durations)
                features['duration_std'] = np.std(durations)
            durations.append((session.iloc[-1, 2] - session.iloc[0, 2] ).seconds)
            # the accurace is the all time wins divided by the all time attempts
            features['accumulated_accuracy'] = accumulated_accuracy/counter if counter > 0 else 0
            accuracy = true_attempts/(true_attempts+false_attempts) if (true_attempts+false_attempts) != 0 else 0
            accumulated_accuracy += accuracy
            last_accuracy_title['acc_' + session_title_text] = accuracy
            # a feature of the current accuracy categorized
            # it is a counter of how many times this player was in each accuracy group
            if accuracy == 0:
                features['accuracy_group'] = 0
            elif accuracy == 1:
                features['accuracy_group'] = 3
            elif accuracy == 0.5:
                features['accuracy_group'] = 2
            else:
                features['accuracy_group'] = 1
            features.update(accuracy_groups)
            accuracy_groups[features['accuracy_group']] += 1
            # mean of the all accuracy groups of this player
            features['accumulated_accuracy_group'] = accumulated_accuracy_group/counter if counter > 0 else 0
            accumulated_accuracy_group += features['accuracy_group']
            # how many actions the player has done so far, it is initialized as 0 and updated some lines below
           
            features['accumulated_actions'] = accumulated_actions
            features['assessment_completed'] = assessment_completed
            features['Cumcount_assessment_completed'] = CumCount_assessment_completed
            assessment_completed = 1 if (session[session['exit_type']=='game_completed'].shape[0]>0) else 0
            CumCount_assessment_completed += assessment_completed
            if session_title_text =="Cauldron Filler (Assessment)":
                features['prev_accuracy_Samegroup'] = int(-1) if cauldron_Filler_assesment=='' else float(cauldron_Filler_assesment[0]+'.'+cauldron_Filler_assesment[1:30])
                cauldron_Filler_assesment = str(features['accuracy_group'])+cauldron_Filler_assesment
                
            elif session_title_text == "Chest Sorter (Assessment)":
                features['prev_accuracy_Samegroup'] = int(-1) if chest_sorter=='' else float(chest_sorter[0]+'.'+chest_sorter[1:30])
                chest_sorter = str(features['accuracy_group'])+chest_sorter
                
                
            elif session_title_text =="Bird Measurer (Assessment)":
                features['prev_accuracy_Samegroup'] = int(-1) if bird_measurer=='' else float(bird_measurer[0]+'.'+bird_measurer[1:30])
                bird_measurer = str(features['accuracy_group'])+bird_measurer
                                  
            elif session_title_text =="Cart Balancer (Assessment)":
                features['prev_accuracy_Samegroup'] = int(-1) if cart_balancer =='' else float(cart_balancer[0]+'.'+cart_balancer[1:30])
                cart_balancer = str(features['accuracy_group'])+cart_balancer                
                                                           
            elif session_title_text=="Mushroom Sorter (Assessment)":
                features['prev_accuracy_Samegroup'] = int(-1) if mushroom_sorter =='' else float(mushroom_sorter[0]+'.'+mushroom_sorter[1:30])
                mushroom_sorter = str(features['accuracy_group'])+mushroom_sorter
                
                
            features['prev_accuracy_group'] = int(-1) if prev_accuracy=='' else float(prev_accuracy[0]+'.'+prev_accuracy[1:30])
            prev_accuracy = str(features['accuracy_group'])+prev_accuracy
            
            features['clip_counter']=clip_counter
            features['game_counter'] = game_counter
            features['activity_counter'] = activity_counter
                
            features['clip_duration'] = clip_duration
            features['game_duration'] = game_duration
            features['activity_duration'] = activity_duration
            
            features['game_mean_duration'] = 0 if game_durations_list==[] else np.nanmean(game_durations_list)
            features['game_std_duraiton'] = 0 if game_durations_list ==[] else np.nanstd(game_durations_list)
            features['game_cumsum_duration'] = cumsum_game_duration
            
            features['clip_mean_duration'] = 0 if clip_durations_list==[] else np.nanmean(clip_durations_list)
            features['clip_std_duraiton'] = 0 if clip_durations_list==[] else np.nanstd(clip_durations_list)
            features['clip_cumsum_duration'] = cumsum_clip_duration
            
            features['activity_mean_duration'] = 0 if activity_durations_list==[] else np.nanmean(activity_durations_list)
            features['activity_std_duraiton'] = 0 if activity_durations_list==[] else np.nanstd(activity_durations_list)
            features['activity_cumsum_duration'] = cumsum_activity_duration
                       
            

            features['correct_true'] = correct_true
            features['correct_false'] = correct_false
            features['game_correct_TrueFalse_ratio'] = correct_true/(correct_false+correct_true) if (correct_true)>0 else 0
            features['correct_ratio'] = 1/(correct_false+1)
            
    
            features['misses_true'] = misses_true
            features['misses_false'] = misses_false
            features['game_misses_TrueFalse_ratio'] = misses_true/(misses_true+misses_false) if (misses_true)>0 else 0
            features['misses_ratio'] = 1/(misses_true+1)
            
            features['game_max_round'] = 0 if game_round_list==[] else np.nanmax(game_round_list)          
            features['game_nunique_round'] = 0 if game_round_list==[] else len(np.unique(game_round_list)) 
            
            
            features['game_max_level'] = 0 if game_level_list==[] else np.nanmax(game_level_list)          
            features['game_nunique_level'] = 0 if game_level_list==[] else len(np.unique(game_level_list))

            
             
            game_level_list = []
            game_correct_list = []
            game_round_list = []
            game_misses_list = []
            
            misses_true = 0
            misses_false = 0
            correct_true = 0
            correct_false = 0 
            game_duration=0
            clip_duration=0
            activity_duration=0
            clip_counter = 0
            game_counter= 0
            activity_counter = 0
    
            # there are some conditions to allow this features to be inserted in the datasets
            # if it's a test set, all sessions belong to the final dataset
            # it it's a train, needs to be passed throught this clausule: session.query(f'event_code == {win_code[session_title]}')
            # that means, must exist an event_code 4100 or 4110
            if test_set:
                all_assessments.append(features)
            elif true_attempts+false_attempts > 0:
                all_assessments.append(features)
            counter += 1
            
            
        elif session_type=="Clip":
            clip_counter +=1
            clip_durations_list.append((clip_time[activities_labels[session_title]]))
            clip_duration += (clip_time[activities_labels[session_title]])
            cumsum_clip_duration +=clip_duration
            
            
        elif session_type=="Game":
            game_counter +=1
            game_durations_list.append((session.iloc[-1]['timestamp'] - session.iloc[0]['timestamp']).seconds)
            game_duration += (session.iloc[-1]['timestamp'] - session.iloc[0]['timestamp']).seconds
            cumsum_game_duration +=game_duration
            correct_true += session[session['correct']==1].shape[0]
            correct_false += session[session['correct']==0].shape[0]
            
            misses_true += session[session["misses"]==1].shape[0]
            misses_false += session[session["misses"]==0].shape[0]
            game_sum_event_count = game_sum_event_count + session['event_count'].iloc[-1]
            def update_counters(counter: dict, col: str):
                num_of_session_count = Counter(session[col])
                for k in num_of_session_count.keys():
                    x = str(k) + '_g'
                    if col == 'title':
                        x = activities_labels[k]
                    counter[x] += num_of_session_count[k]
                return counter
            
            game_event_code_count = update_counters(game_event_code_count, "event_code")
            
            
            game_correct_list.extend(session['correct'])
            game_round_list.extend(session['round'])
            game_level_list.extend(session['level'])
            game_misses_list.extend(session["misses"])
            
        elif session_type=="Activity":
            activity_counter +=1
            activity_durations_list.append((session.iloc[-1]['timestamp'] - session.iloc[0]['timestamp']).seconds)
            activity_duration += (session.iloc[-1]['timestamp'] - session.iloc[0]['timestamp']).seconds
            cumsum_activity_duration +=game_duration
            Activity_sum_event_count = Activity_sum_event_count + session['event_count'].iloc[-1]
            def update_counters(counter: dict, col: str):
                num_of_session_count = Counter(session[col])
                for k in num_of_session_count.keys():
                    x = str(k) + '_A'
                    if col == 'title':
                        x = activities_labels[k]
                    counter[x] += num_of_session_count[k]
                return counter
            Activity_event_code_count = update_counters(Activity_event_code_count, "event_code")            
            
        sessions_count += 1
        # this piece counts how many actions was made in each event_code so far
        def update_counters(counter: dict, col: str):
                num_of_session_count = Counter(session[col])
                for k in num_of_session_count.keys():
                    x = k
                    if col == 'title':
                        x = activities_labels[k]
                    counter[x] += num_of_session_count[k]
                return counter
        
        event_code_count = update_counters(event_code_count, "event_code")
        event_id_count = update_counters(event_id_count, "event_id")
        title_count = update_counters(title_count, 'title')
        title_event_code_count = update_counters(title_event_code_count, 'title_event_code')
        
        # counts how many actions the player has done so far, used in the feature of the same name
        accumulated_actions += len(session)
        if last_activity != session_type:
            user_activities_count[session_type] += 1
            last_activitiy = session_type 
                         
    # if it't the test_set, only the last assessment must be predicted, the previous are scraped
    if test_set:
        return all_assessments[-1]
    # in the train_set, all assessments goes to the dataset
    return all_assessments

In [15]:
# The following 3 functions have been taken from Ben Hamner's github repository
# https://github.com/benhamner/Metrics
def confusion_matrix(rater_a, rater_b, min_rating=None, max_rating=None):
    """
    Returns the confusion matrix between rater's ratings
    """
    assert(len(rater_a) == len(rater_b))
    if min_rating is None:
        min_rating = min(rater_a + rater_b)
    if max_rating is None:
        max_rating = max(rater_a + rater_b)
    num_ratings = int(max_rating - min_rating + 1)
    conf_mat = [[0 for i in range(num_ratings)]
                for j in range(num_ratings)]
    for a, b in zip(rater_a, rater_b):
        conf_mat[a - min_rating][b - min_rating] += 1
    return conf_mat


def histogram(ratings, min_rating=None, max_rating=None):
    """
    Returns the counts of each type of rating that a rater made
    """
    if min_rating is None:
        min_rating = min(ratings)
    if max_rating is None:
        max_rating = max(ratings)
    num_ratings = int(max_rating - min_rating + 1)
    hist_ratings = [0 for x in range(num_ratings)]
    for r in ratings:
        hist_ratings[r - min_rating] += 1
    return hist_ratings


def qwk(y, y_pred):
    """
    Calculates the quadratic weighted kappa
    axquadratic_weighted_kappa calculates the quadratic weighted kappa
    value, which is a measure of inter-rater agreement between two raters
    that provide discrete numeric ratings.  Potential values range from -1
    (representing complete disagreement) to 1 (representing complete
    agreement).  A kappa value of 0 is expected if all agreement is due to
    chance.
    quadratic_weighted_kappa(rater_a, rater_b), where rater_a and rater_b
    each correspond to a list of integer ratings.  These lists must have the
    same length.
    The ratings should be integers, and it is assumed that they contain
    the complete range of possible ratings.
    quadratic_weighted_kappa(X, min_rating, max_rating), where min_rating
    is the minimum possible rating, and max_rating is the maximum possible
    rating
    """
    rater_a = y
    rater_b = y_pred
    min_rating=None
    max_rating=None
    rater_a = np.array(rater_a, dtype=int)
    rater_b = np.array(rater_b, dtype=int)
    assert(len(rater_a) == len(rater_b))
    if min_rating is None:
        min_rating = min(min(rater_a), min(rater_b))
    if max_rating is None:
        max_rating = max(max(rater_a), max(rater_b))
    conf_mat = confusion_matrix(rater_a, rater_b,
                                min_rating, max_rating)
    num_ratings = len(conf_mat)
    num_scored_items = float(len(rater_a))

    hist_rater_a = histogram(rater_a, min_rating, max_rating)
    hist_rater_b = histogram(rater_b, min_rating, max_rating)

    numerator = 0.0
    denominator = 0.0

    for i in range(num_ratings):
        for j in range(num_ratings):
            expected_count = (hist_rater_a[i] * hist_rater_b[j]
                              / num_scored_items)
            d = pow(i - j, 2.0) / pow(num_ratings - 1, 2.0)
            numerator += d * conf_mat[i][j] / num_scored_items
            denominator += d * expected_count / num_scored_items

    return (1.0 - numerator / denominator)

In [16]:
def get_train_and_test(train, test):
    compiled_train = []
    compiled_test = []
    for i, (ins_id, user_sample) in tqdm(enumerate(train.groupby('installation_id', sort = False)), total = 17000):
        compiled_train += get_data(user_sample)
    for ins_id, user_sample in tqdm(test.groupby('installation_id', sort = False), total = 1000):
        test_data = get_data(user_sample, test_set = True)
        compiled_test.append(test_data)
    reduce_train = pd.DataFrame(compiled_train)
    reduce_test = pd.DataFrame(compiled_test)
    categoricals = ['session_title']
    
    compiled_test_his = []
    for i, (ins_id, user_sample) in tqdm(enumerate(test.groupby('installation_id', sort = False)), total = 1000):
        compiled_test_his += get_data(user_sample)
    reduce_test_his = pd.DataFrame(compiled_test_his)
    
    return reduce_train, reduce_test, categoricals, reduce_test_his

In [17]:
class OptimizedRounder(object):
    def _init_(self):
        self.coef_ = 0

    def _kappa_loss(self, coef, X, y):
        X_p = np.copy(X)
        for i, pred in enumerate(X_p):
            if pred < coef[0]:
                X_p[i] = 0
            elif pred >= coef[0] and pred < coef[1]:
                X_p[i] = 1
            elif pred >= coef[1] and pred < coef[2]:
                X_p[i] = 2
            elif pred >= coef[2] and pred < coef[3]:
                X_p[i] = 3
            else:
                X_p[i] = 4

        ll = metrics.cohen_kappa_score(y, X_p, weights='quadratic')
        return -ll

    def fit(self, X, y):
        loss_partial = partial(self._kappa_loss, X=X, y=y)
        initial_coef = [0.5, 1.5, 2.5, 3.5]
        self.coef_ = sp.optimize.minimize(loss_partial, initial_coef, method='nelder-mead')

    def predict(self, X, coef):
        X_p = np.copy(X)
        for i, pred in enumerate(X_p):
            if pred < coef[0]:
                X_p[i] = 0
            elif pred >= coef[0] and pred < coef[1]:
                X_p[i] = 1
            elif pred >= coef[1] and pred < coef[2]:
                X_p[i] = 2
            elif pred >= coef[2]:
                X_p[i] = 3
            else:
                X_p[i] = 4
        return X_p

    def coefficients(self):
        return self.coef_['x']

In [18]:
def sample(seed):
    ## sample
    his_idx = []
    reduce_train_origin = reduce_train.copy()
    used_idx = []
    from tqdm import tqdm_notebook, tqdm
    import random
    random.seed(seed)
    np.random.seed(seed)
    for iid in tqdm_notebook(set(reduce_train_origin[Id])):
        list_ = list(reduce_train_origin.loc[reduce_train_origin[Id] == iid].index)
    #     print(list_)

        cur = np.random.choice(list_, 1)[0]
        cur_target = reduce_train_origin.loc[cur, target]
        his = [x for x in list_ if x < cur]
        his_idx.append([his, cur_target])

        used_idx.append(cur)
    print(len(used_idx))
    train_feature = pd.DataFrame()
    for i in tqdm_notebook(range(len(his_idx))):
        temp_feature = reduce_train_origin.loc[his_idx[i][0]]
        train_feature = train_feature.append(temp_feature)
    return train_feature.index
 

In [19]:
class Base_Model(object):
    
    def __init__(self, train_df, test_df, features, categoricals=[], n_splits=5, verbose=True):
        self.train_df = train_df
        self.test_df = test_df
        self.features = features
        self.n_splits = n_splits
        self.categoricals = categoricals
        self.target = 'accuracy_group'
        self.cv = self.get_cv()
        self.verbose = verbose
        self.params = self.get_params()
        self.y_pred, self.score, self.model, self.full_oof = self.fit()
        
    def train_model(self, train_set, val_set):
        raise NotImplementedError
        
    def get_cv(self):
        cv = StratifiedKFold(n_splits=self.n_splits, shuffle=False, random_state=42)
        return cv.split(self.train_df, self.train_df[self.target])
    
    def get_params(self):
        raise NotImplementedError
        
    def convert_dataset(self, x_train, y_train, x_val, y_val):
        raise NotImplementedError
        
    def convert_x(self, x):
        return x
        
    def fit(self):
        seeds = [2119, 1031, 190, 13192, 23123, 5603]
        full_oof = np.zeros((len(reduce_train), ))
        y_pred = np.zeros((len(reduce_test), ))
        for seed in seeds:
            print(f"Seed :- {seed}")
            cv = GroupKFold(n_splits=self.n_splits)
            oof_pred = np.zeros((len(reduce_train), ))
            for fold, (train_idx, val_idx) in enumerate(cv.split(self.train_df,self.train_df[self.target],self.train_df["installation_id"])):
                x_train, x_val = self.train_df[self.features].iloc[train_idx], self.train_df[self.features].iloc[val_idx]
                y_train, y_val = self.train_df[self.target][train_idx], self.train_df[self.target][val_idx]
                train_set, val_set = self.convert_dataset(x_train, y_train, x_val, y_val)
                model = self.train_model(train_set, val_set)
                conv_x_val = self.convert_x(x_val)
                oof_pred[val_idx] = model.predict(conv_x_val).reshape(oof_pred[val_idx].shape)
                x_test = self.convert_x(self.test_df[self.features])
                y_pred += model.predict(x_test).reshape(y_pred.shape) / (5*len(seeds))
                print('Partial score of fold {} is: {}'.format(fold, eval_qwk_lgb_regr(y_val, oof_pred[val_idx])[1]))
            _, loss_score, _ = eval_qwk_lgb_regr(self.train_df[self.target], oof_pred)
            if self.verbose:
                print('Our oof cohen kappa score is: ', loss_score)
            full_oof += oof_pred/len(seeds)
            print('\n\n')
        print('Final oof cohen kappa score is: ', eval_qwk_lgb_regr(self.train_df[self.target], full_oof))
        return y_pred, loss_score, model , full_oof

In [20]:
class Lgb_Model(Base_Model):
    
    def train_model(self, train_set, val_set):
        verbosity = 100 if self.verbose else 0
        return lgb.train(self.params, train_set,num_boost_round=5000, valid_sets=[train_set, val_set], verbose_eval=150,early_stopping_rounds=100)
        
    def convert_dataset(self, x_train, y_train, x_val, y_val):
        train_set = lgb.Dataset(x_train, y_train, categorical_feature=self.categoricals)
        val_set = lgb.Dataset(x_val, y_val, categorical_feature=self.categoricals)
        return train_set, val_set
        
    def get_params(self):
        params ={'n_estimators':5000,
                    'boosting_type': 'gbdt',
                    'objective': 'regression',
                    'metric': 'rmse',
                    'subsample': 0.75,
                    'subsample_freq': 1,
                    'learning_rate': 0.01,
                    'feature_fraction': 0.9,
                    'max_depth': 15,
                    'lambda_l1': 1,  
                    'lambda_l2': 1,
                    'early_stopping_rounds': 100
                    }
        return params

In [21]:
class Xgb_Model(Base_Model):
    
    def train_model(self, train_set, val_set):
        verbosity = 100 if self.verbose else 0
        return xgb.train(self.params, train_set, 
                         num_boost_round=5000, evals=[(train_set, 'train'), (val_set, 'val')], 
                         verbose_eval=verbosity, early_stopping_rounds=100)
        
    def convert_dataset(self, x_train, y_train, x_val, y_val):
        train_set = xgb.DMatrix(x_train, y_train)
        val_set = xgb.DMatrix(x_val, y_val)
        return train_set, val_set
    
    def convert_x(self, x):
        return xgb.DMatrix(x)
        
    def get_params(self):
        params = {'colsample_bytree': 0.8,                 
            'learning_rate': 0.01,
            'max_depth': 10,
            'subsample': 1,
            'objective':'reg:squarederror',
            #'eval_metric':'rmse',
            'min_child_weight':3,
            'gamma':0.25,
            'n_estimators':5000}


        return params


In [22]:
# tranform function to get the train and test set
reduce_train, reduce_test, categoricals, reduce_test_his = get_train_and_test(train, test)

In [23]:
reduce_train['activity_timeDuration'] = (reduce_train['clip_duration'])+(reduce_train['activity_duration'])+(reduce_train['game_duration'])
reduce_test['activity_timeDuration'] = (reduce_test['clip_duration'])+(reduce_test['activity_duration'])+(reduce_test['game_duration'])
reduce_test_his['activity_timeDuration'] = (reduce_test_his['clip_duration'])+(reduce_test_his['activity_duration'])+(reduce_test_his['game_duration'])


In [24]:
reduce_train.head(1)

Clip  Activity  Assessment  Game  acc_12 Monkeys  acc_Air Show  \
0    11         3           0     4              -1            -1   

   acc_All Star Sorting  acc_Balancing Act  acc_Bird Measurer (Assessment)  \
0                    -1                 -1                            -1.0   

   acc_Bottle Filler (Activity)  acc_Bubble Bath  acc_Bug Measurer (Activity)  \
0                            -1               -1                           -1   

   acc_Cart Balancer (Assessment)  acc_Cauldron Filler (Assessment)  \
0                            -1.0                              -1.0   

   acc_Chest Sorter (Assessment)  acc_Chicken Balancer (Activity)  \
0                           -1.0                               -1   

   acc_Chow Time  acc_Costume Box  acc_Crystal Caves - Level 1  \
0             -1               -1                           -1   

   acc_Crystal Caves - Level 2  acc_Crystal Caves - Level 3  \
0                           -1                           -1   

   acc_Crystals Rule  acc_Dino Dive  acc_Dino Drink  \
0                 -1             -1              -1   

   acc_Egg Dropper (Activity)  acc_Fireworks (Activity)  \
0                          -1                        -1   

   acc_Flower Waterer (Activity)  acc_Happy Camel  \
0                             -1               -1   

   acc_Heavy, Heavier, Heaviest  acc_Honey Cake  acc_Leaf Leader  \
0                            -1              -1               -1   

   acc_Lifting Heavy Things  acc_Magma Peak - Level 1  \
0                        -1                        -1   

   acc_Magma Peak - Level 2  acc_Mushroom Sorter (Assessment)  \
0                        -1                              -1.0   

   acc_Ordering Spheres  acc_Pan Balance  acc_Pirate's Tale  acc_Rulers  \
0                    -1               -1                 -1          -1   

   acc_Sandcastle Builder (Activity)  acc_Scrub-A-Dub  acc_Slop Problem  \
0                                 -1               -1                -1   

   acc_Treasure Map  acc_Tree Top City - Level 1  acc_Tree Top City - Level 2  \
0                -1                           -1                           -1   

   acc_Tree Top City - Level 3  acc_Watering Hole (Activity)  \
0                           -1                            -1   

   acc_Welcome to Lost Lagoon!  2000  2010  2020  2025  2030  2035  2040  \
0                           -1    18     0    20     4    18     0     6   

   2050  2060  2070  2075  2080  2081  2083  3010  3020  3021  3110  3120  \
0     6     0     0     0     4     1     2    79     7     9    77     7   

   3121  4010  4020  4021  4022  4025  4030  4031  4035  4040  4045  4050  \
0     9     4    92    14    31    19   121     0     1     0     0     0   

   4070  4080  4090  4095  4100  4110  4220  4230  4235  5000  5010  003cd2ee  \
0    94     0     4     0     0     0     0     0     0     0     0         0   

   0086365d  00c73085  01ca3a3c  022b4259  02a42007  0330ab6a  0413e89d  \
0         0         0         0         0        23         0         0   

   04df9b66  05ad839b  06372577  070a5291  08fd73f3  08ff79ad  0a08139c  \
0         0         0         0         0        15         0         0   

   0ce40006  0d18d96c  0d1da71f  0db6d71d  119b5b02  1325467d  1340b8d7  \
0         0         0         0         0         0        18         0   

   1375ccb7  13f56524  14de4c5d  155f62a4  1575e76c  15a43e5b  15ba1109  \
0         0         0         0         0         0         0         0   

   15eb4a7d  15f99afc  160654fd  16667cc5  16dffff1  17113b36  17ca3959  \
0         0         0         0         0         0         0         0   

   19967db1  1996c610  1af8be29  1b54d27f  1bb5fbdb  1beb320a  1c178d24  \
0         0         0         0         0        19         0         0   

   1cc7cfca  1cf54632  1f19558b  222660ff  2230fab4  250513af  25fa8af4  \
0        27         0         3         0         0         0         0   

   26

In [25]:
reduce_train['activity_counter'] = (1*reduce_train['Clip'])+(2*reduce_train['Activity'])+(3*reduce_train['Game'])+(5*reduce_train['Assessment'])
reduce_test['activity_counter'] = (1*reduce_test['Clip'])+(2*reduce_test['Activity'])+(3*reduce_test['Game'])+(5*reduce_test['Assessment'])
reduce_test_his['activity_counter'] = (1*reduce_test_his['Clip'])+(2*reduce_test_his['Activity'])+(3*reduce_test_his['Game'])+(5*reduce_test_his['Assessment'])

In [26]:
reduce_train['counter'] = (1*reduce_train['clip_counter'])+(2*reduce_train['activity_counter'])+(3*reduce_train['game_counter'])
reduce_test['counter'] = (1*reduce_test['clip_counter'])+(2*reduce_test['activity_counter'])+(3*reduce_test['game_counter'])
reduce_test_his['counter'] = (1*reduce_test_his['clip_counter'])+(2*reduce_test_his['activity_counter'])+(3*reduce_test_his['game_counter'])


In [27]:
reduce_train.head()

Clip  Activity  Assessment  Game  acc_12 Monkeys  acc_Air Show  \
0    11         3           0     4              -1            -1   
1    14         4           1     6              -1            -1   
2    14         4           2     6              -1            -1   
3    24         9           4    10              -1            -1   
4    28        10           5    13              -1            -1   

   acc_All Star Sorting  acc_Balancing Act  acc_Bird Measurer (Assessment)  \
0                    -1                 -1                            -1.0   
1                    -1                 -1                            -1.0   
2                    -1                 -1                             0.0   
3                    -1                 -1                             0.0   
4                    -1                 -1                             0.0   

   acc_Bottle Filler (Activity)  acc_Bubble Bath  acc_Bug Measurer (Activity)  \
0                            -1               -1                           -1   
1                            -1               -1                           -1   
2                            -1               -1                           -1   
3                            -1               -1                           -1   
4                            -1               -1                           -1   

   acc_Cart Balancer (Assessment)  acc_Cauldron Filler (Assessment)  \
0                            -1.0                              -1.0   
1                            -1.0                              -1.0   
2                            -1.0                              -1.0   
3                            -1.0                              -1.0   
4                            -1.0                              -1.0   

   acc_Chest Sorter (Assessment)  acc_Chicken Balancer (Activity)  \
0                           -1.0                               -1   
1                           -1.0                               -1   
2                           -1.0                               -1   
3                           -1.0                               -1   
4                           -1.0                               -1   

   acc_Chow Time  acc_Costume Box  acc_Crystal Caves - Level 1  \
0             -1               -1                           -1   
1             -1               -1                           -1   
2             -1               -1                           -1   
3             -1               -1                           -1   
4             -1               -1                           -1   

   acc_Crystal Caves - Level 2  acc_Crystal Caves - Level 3  \
0                           -1                           -1   
1                           -1                           -1   
2                           -1                           -1   
3                           -1                           -1   
4                           -1                           -1   

   acc_Crystals Rule  acc_Dino Dive  acc_Dino Drink  \
0                 -1             -1              -1   
1                 -1             -1              -1   
2                 -1             -1              -1   
3                 -1             -1              -1   
4                 -1             -1              -1   

   acc_Egg Dropper (Activity)  acc_Fireworks (Activity)  \
0                          -1                        -1   
1                          -1                        -1   
2                          -1                        -1   
3                          -1                        -1   
4                          -1                        -1   

   acc_Flower Waterer (Activity)  acc_Happy Camel  \
0                             -1               -1   
1                             -1               -1   
2                             -1               -1   
3                             -1               -1   
4                             -1               -1   

   acc_He

In [28]:
reduce_test.head(100)

Clip  Activity  Assessment  Game  acc_12 Monkeys  acc_Air Show  \
0     14         7           1     3              -1            -1   
1     29        11           5    12              -1            -1   
2      6         2           0     0              -1            -1   
3     10         2           0     1              -1            -1   
4     17         1           0     6              -1            -1   
5      6         4           1     2              -1            -1   
6     13         2           0     5              -1            -1   
7     17         9           9     7              -1            -1   
8     10         3           3     5              -1            -1   
9     15         0           0     1              -1            -1   
10     3         1           0     1              -1            -1   
11     7         2           0     1              -1            -1   
12    16         2           3     3              -1            -1   
13     4         1           0     1              -1            -1   
14    10         1           0     1              -1            -1   
15     5         3           1     0              -1            -1   
16     3         1           0     0              -1            -1   
17    11         3           1     3              -1            -1   
18     3         1           0     2              -1            -1   
19     2         0           0     0              -1            -1   
20    22         8           5    11              -1            -1   
21    16         8           1     2              -1            -1   
22     4         5           0     7              -1            -1   
23    73        31          14    45              -1            -1   
24     0         1           0     0              -1            -1   
25    11         6           2     4              -1            -1   
26    23         3           9    10              -1            -1   
27     7         0           1     0              -1            -1   
28     3         0           0     0              -1            -1   
29     0         1           0     0              -1            -1   
30    51        36          16    43              -1            -1   
31     7         0           1     0              -1            -1   
32    15         2           2     0              -1            -1   
33    16         1           7    14              -1            -1   
34     9         7           4     5              -1            -1   
35     1         0           1     0              -1            -1   
36     7         2           0     2              -1            -1   
37     9         0           0     0              -1            -1   
38   144        31          22    34              -1            -1   
39    22         6           7    13              -1            -1   
40     9         2           0     4              -1            -1   
41    43        17          30     0              -1            -1   
42     7         2           1     4              -1            -1   
43    14         0           1     2              -1            -1   
44     4         2           0     4              -1            -1   
45     6         4           1     6              -1            -1   
46     9         6           6     6              -1            -1   
47    25         8           1     4              -1            -1   
48     3         1           0     1              -1            -1   
49    18         4           2     5              -1            -1   
50    12         0           1     1              -1            -1   
51     3        13           2     0              -1            -1   
52     6         1           0     2              -1            -1   
53     2         1           0     1              -1            -1   
54    31         5           4     6              -1            -1   
55   103        17           7    36              -1            -1   
56    16      

In [29]:
reduce_train = reduce_train.drop(columns=['assessment_type'])
reduce_test = reduce_test.drop(columns=['assessment_type'])
reduce_test_his = reduce_test_his.drop(columns=['assessment_type'])

In [30]:
reduce_train['Clip']

0        11
1        14
2        14
3        24
4        28
         ..
17685    26
17686     3
17687    11
17688    23
17689    24
Name: Clip, Length: 17690, dtype: int64

In [31]:
train.shape[0]

11341042

In [32]:
reduce_train.head()

Clip  Activity  Assessment  Game  acc_12 Monkeys  acc_Air Show  \
0    11         3           0     4              -1            -1   
1    14         4           1     6              -1            -1   
2    14         4           2     6              -1            -1   
3    24         9           4    10              -1            -1   
4    28        10           5    13              -1            -1   

   acc_All Star Sorting  acc_Balancing Act  acc_Bird Measurer (Assessment)  \
0                    -1                 -1                            -1.0   
1                    -1                 -1                            -1.0   
2                    -1                 -1                             0.0   
3                    -1                 -1                             0.0   
4                    -1                 -1                             0.0   

   acc_Bottle Filler (Activity)  acc_Bubble Bath  acc_Bug Measurer (Activity)  \
0                            -1               -1                           -1   
1                            -1               -1                           -1   
2                            -1               -1                           -1   
3                            -1               -1                           -1   
4                            -1               -1                           -1   

   acc_Cart Balancer (Assessment)  acc_Cauldron Filler (Assessment)  \
0                            -1.0                              -1.0   
1                            -1.0                              -1.0   
2                            -1.0                              -1.0   
3                            -1.0                              -1.0   
4                            -1.0                              -1.0   

   acc_Chest Sorter (Assessment)  acc_Chicken Balancer (Activity)  \
0                           -1.0                               -1   
1                           -1.0                               -1   
2                           -1.0                               -1   
3                           -1.0                               -1   
4                           -1.0                               -1   

   acc_Chow Time  acc_Costume Box  acc_Crystal Caves - Level 1  \
0             -1               -1                           -1   
1             -1               -1                           -1   
2             -1               -1                           -1   
3             -1               -1                           -1   
4             -1               -1                           -1   

   acc_Crystal Caves - Level 2  acc_Crystal Caves - Level 3  \
0                           -1                           -1   
1                           -1                           -1   
2                           -1                           -1   
3                           -1                           -1   
4                           -1                           -1   

   acc_Crystals Rule  acc_Dino Dive  acc_Dino Drink  \
0                 -1             -1              -1   
1                 -1             -1              -1   
2                 -1             -1              -1   
3                 -1             -1              -1   
4                 -1             -1              -1   

   acc_Egg Dropper (Activity)  acc_Fireworks (Activity)  \
0                          -1                        -1   
1                          -1                        -1   
2                          -1                        -1   
3                          -1                        -1   
4                          -1                        -1   

   acc_Flower Waterer (Activity)  acc_Happy Camel  \
0                             -1               -1   
1                             -1               -1   
2                             -1               -1   
3                             -1               -1   
4                             -1               -1   

   acc_He

In [33]:
categoricals = ['session_title']

In [34]:
# call feature engineering function
features = reduce_train.loc[(reduce_train.sum(axis=1) != 0), (reduce_train.sum(axis=0) != 0)].columns # delete useless columns
features = [x for x in features if x not in ['accuracy_group', 'installation_id']]

In [35]:
to_exclude = [] 
ajusted_test = reduce_test.copy()
for feature in ajusted_test.columns:
    if feature not in ['clip_duration','activity_duration','game_duration','activity_counter','misses_false','misses_true','correct_true','correct_false','counter','accuracy_group', 'installation_id', 'accuracy_group', 'session_title','prev_accuracy_group','prev_accuracy_Samegroup','clip_counter','game_counter','game_max_level','game_nunique_level','game_max_round','game_nunique_round']:
        data = reduce_train[feature]
        train_mean = data.median()
        data = ajusted_test[feature] 
        test_mean = data.median()
        try:
            error = stract_hists(feature, adjust=True)
            ajust_factor = train_mean / test_mean
            if ajust_factor > 10 or ajust_factor < 0.1:# or error > 0.01:
                to_exclude.append(feature)
                print(feature, train_mean, test_mean, error)
            else:
                ajusted_test[feature] *= ajust_factor
        except:
            to_exclude.append(feature)
            print(feature, train_mean, test_mean)

Clip 16.0 8.0
Activity 5.0 2.0
Assessment 3.0 1.0
Game 6.0 2.0
acc_12 Monkeys -1.0 -1.0
acc_Air Show -1.0 -1.0
acc_All Star Sorting -1.0 -1.0
acc_Balancing Act -1.0 -1.0
acc_Bird Measurer (Assessment) -1.0 -1.0
acc_Bottle Filler (Activity) -1.0 -1.0
acc_Bubble Bath -1.0 -1.0
acc_Bug Measurer (Activity) -1.0 -1.0
acc_Cart Balancer (Assessment) 0.0 -1.0
acc_Cauldron Filler (Assessment) 0.0 -1.0
acc_Chest Sorter (Assessment) -1.0 -1.0
acc_Chicken Balancer (Activity) -1.0 -1.0
acc_Chow Time -1.0 -1.0
acc_Costume Box -1.0 -1.0
acc_Crystal Caves - Level 1 -1.0 -1.0
acc_Crystal Caves - Level 2 -1.0 -1.0
acc_Crystal Caves - Level 3 -1.0 -1.0
acc_Crystals Rule -1.0 -1.0
acc_Dino Dive -1.0 -1.0
acc_Dino Drink -1.0 -1.0
acc_Egg Dropper (Activity) -1.0 -1.0
acc_Fireworks (Activity) -1.0 -1.0
acc_Flower Waterer (Activity) -1.0 -1.0
acc_Happy Camel -1.0 -1.0
acc_Heavy, Heavier, Heaviest -1.0 -1.0
acc_Honey Cake -1.0 -1.0
acc_Leaf Leader -1.0 -1.0
acc_Lifting Heavy Things -1.0 -1.0
acc_Magma Peak - L

In [36]:

reduce_train[features].shape

(17690, 1015)

In [37]:
# debug for "LightGBMError: Do not support special JSON characters in feature name."
features = ["".join (c if c.isalnum() else "_" for c in str(x)) for x in features]
reduce_train.columns = ["".join (c if c.isalnum() else "_" for c in str(x)) for x in reduce_train.columns]
reduce_test.columns  = ["".join (c if c.isalnum() else "_" for c in str(x)) for x in reduce_test.columns]
ajusted_test.columns = ["".join (c if c.isalnum() else "_" for c in str(x)) for x in ajusted_test.columns]

In [38]:
features = sorted(features)

In [39]:
#cat_model = Catb_Model(reduce_train, ajusted_test, features, categoricals=categoricals)
lgb_model = Lgb_Model(reduce_train, ajusted_test, features, categoricals=categoricals)
xgb_model = Xgb_Model(reduce_train, ajusted_test, features, categoricals=categoricals)

Seed :- 2119
Training until validation scores don't improve for 100 rounds
[150]	training's rmse: 0.980006	valid_1's rmse: 1.01372
[300]	training's rmse: 0.918579	valid_1's rmse: 0.980294
[450]	training's rmse: 0.884087	valid_1's rmse: 0.972557
[600]	training's rmse: 0.857284	valid_1's rmse: 0.969011
[750]	training's rmse: 0.833477	valid_1's rmse: 0.967856
[900]	training's rmse: 0.811576	valid_1's rmse: 0.967202
[1050]	training's rmse: 0.79149	valid_1's rmse: 0.966849
Early stopping, best iteration is:
[1026]	training's rmse: 0.794581	valid_1's rmse: 0.966736
Partial score of fold 0 is: 0.6064934494489109
Training until validation scores don't improve for 100 rounds
[150]	training's rmse: 0.981642	valid_1's rmse: 1.01453
[300]	training's rmse: 0.920116	valid_1's rmse: 0.979456
[450]	training's rmse: 0.885869	valid_1's rmse: 0.971307
[600]	training's rmse: 0.85874	valid_1's rmse: 0.968567
[750]	training's rmse: 0.835229	valid_1's rmse: 0.967718
[900]	training's rmse: 0.813629	valid_1's 

In [40]:
from functools import partial
import scipy as sp
class OptimizedRounder(object):
    """
    An optimizer for rounding thresholds
    to maximize Quadratic Weighted Kappa (QWK) score
    # https://www.kaggle.com/naveenasaithambi/optimizedrounder-improved
    """
    def __init__(self):
        self.coef_ = 0

    def _kappa_loss(self, coef, X, y):
        """
        Get loss according to
        using current coefficients
        
        :param coef: A list of coefficients that will be used for rounding
        :param X: The raw predictions
        :param y: The ground truth labels
        """
        X_p = pd.cut(X, [-np.inf] + list(np.sort(coef)) + [np.inf], labels = [0, 1, 2, 3])

        return -qwk(y, X_p)

    def fit(self, X, y,random_flg=False):
        """
        Optimize rounding thresholds
        
        :param X: The raw predictions
        :param y: The ground truth labels
        """
        loss_partial = partial(self._kappa_loss, X=X, y=y)
        # [1.09830188 1.67317237 2.17390658]
        if random_flg:
            initial_coef = [np.random.uniform(0.5,0.6), np.random.uniform(0.6,0.7), np.random.uniform(0.8,0.9)]
        else:
            initial_coef = [0.5, 1.5, 2.5]
        self.coef_ = sp.optimize.minimize(loss_partial, initial_coef, method='nelder-mead')

    def predict(self, X, coef):
        """
        Make predictions with specified thresholds
        
        :param X: The raw predictions
        :param coef: A list of coefficients that will be used for rounding
        """
        return pd.cut(X, [-np.inf] + list(np.sort(coef)) + [np.inf], labels = [0, 1, 2, 3])


    def coefficients(self):
        """
        Return the optimized coefficients
        """
        return self.coef_['x']

In [41]:
full_oof = (lgb_model.full_oof*0.8)+(xgb_model.full_oof*0.2)

best_score = 0
for i in tqdm(range(100)):
    optR = OptimizedRounder()
    optR.fit(full_oof, reduce_train[target],random_flg=True)
    coefficients = optR.coefficients()
    opt_preds1 = optR.predict(full_oof, coefficients)
    score = qwk(reduce_train[target], opt_preds1)
    if score > best_score:
        best_score = score
        best_coefficients = coefficients
print(best_score)
print(best_coefficients)

In [ ]:
best_coefficients = [1.11283372 1.70558287 2.11869835]

In [43]:
oof_ = pd.cut(full_oof, [-np.inf] + list(np.sort(best_coefficients)) + [np.inf], labels = [0, 1, 2, 3])
qwk(reduce_train[target],oof_)

0.606817850780381

In [44]:
weights = {'lgb': 0.80, 'cat': 0, 'xgb': 0.20, 'nn': 0.20}
final_pred = (lgb_model.y_pred*weights["lgb"])+(xgb_model.y_pred*weights["xgb"])

In [45]:
optR = OptimizedRounder()

In [46]:
f_pred = pd.cut(final_pred, [-np.inf] + list(np.sort(best_coefficients)) + [np.inf], labels = [0, 1, 2, 3])
sample_submission['accuracy_group'] = f_pred
sample_submission.to_csv('submission.csv', index=False)
sample_submission['accuracy_group'].value_counts(normalize=True)

3    0.524
2    0.185
0    0.162
1    0.129
Name: accuracy_group, dtype: float64

In [47]:
lgb_model.feature_importances.to_csv("feature_importance.csv",index=False)

AttributeError: 'Lgb_Model' object has no attribute 'feature_importances'

In [48]:
from IPython.display import FileLinks,FileLink
FileLinks('.')

./
  __notebook__.ipynb
  train_extras.pkl
  submission.csv
  test_extras.pkl